# Import library

In [1]:
import os
import os, sys
import glob
import re
import datetime
from datetime import datetime, timedelta 
import math, copy, time
from itertools import cycle
from collections import defaultdict

from parse import parse
import numpy as np
import pandas as pd

import torch
from torch import nn, optim
from torch.autograd import Variable
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
import torch.nn.functional as F

# import torchvision
# import torchvision.transforms as transforms

from sklearn.metrics import roc_auc_score, plot_roc_curve
from sklearn import svm


from tqdm.notebook import tqdm

import matplotlib.pyplot as plt
import seaborn

%load_ext autoreload
%autoreload 2

/Users/mckim/miniconda3/envs/py38/lib/python3.8/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.3
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [2]:
pd.set_option("display.max_column", 100)

In [3]:
# Util functions
def size_and_ratio(df, col, dropna=True):
    if pd.__version__ > '1.1':
        sr = df.groupby(col, dropna=dropna).size().sort_values(ascending=False)
    elif dropna:
        sr = df.groupby(col).size().sort_values(ascending=False)
    else:  # dropna == False
        sr = df.fillna('nan').groupby(col).size().sort_values(ascending=False)
    sr_ratio = sr.copy() / sum(sr)
    print("Sum :", sum(sr), sr.shape)
    sr.name = 'size'
    sr_ratio.name = 'ratio'
    return pd.concat([sr, sr_ratio], axis=1)

# Data load

In [4]:
df_train = pd.read_csv("data/df_data_v3_1/df_train_v3_1.csv")
df_val = pd.read_csv("data/df_data_v3_1/df_valid_v3_1.csv")
df_test = pd.read_csv("data/df_data_v3_1/df_test_v3_1.csv")
print(df_train.shape, df_val.shape, df_test.shape)
df_train.head()

(14093, 24) (4647, 24) (4586, 24)


baby_id  cough  fever  sore_throat  shortness_of_breath  head_ache  \
0    21099      1      0            0                    0          1   
1    21151      0      0            1                    0          1   
2    21024      0      0            1                    0          1   
3    21176      0      0            1                    0          1   
4     4467      0      0            1                    0          1   

   runny_nose  muscle_pain  chills  loss_of_taste  loss_of_smell  sputum  \
0           0            0       0              0              0       1   
1           0            0       0              0              0       0   
2           0            0       0              0              0       0   
3           0            0       0              0              0       0   
4           0            0       0              0              0       0   

   chest_pain  indication_other  indication_abroad  indication_contact  \
0           0                 0                  0                   1   
1           0                 0                  0                   1   
2           0                 1                  0                   0   
3           0                 1                  0                   0   
4           0                 1                  0                   0   

   global_confirmed_ratio  confirmed_ratio  sigungu_confirmed_ratio  mask  \
0                0.173311         0.007956                 0.012987     1   
1                0.179009         0.008614                 0.013084     1   
2                0.179009         0.008614                 0.013084     1   
3                0.131500         0.008252                 0.000000     0   
4                0.131500         0.008252                 0.000000     0   

   gender  age_ratio  weekday  pcr_result  
0     0.0       0.18        3           0  
1     0.0       0.17        4           0  
2     1.0       0.29        4           0  
3     0.0       0.40        5           0  
4     1.0       0.34        5           0

### Add CLS token

In [5]:
df_train['[CLS]'] = 0
df_val['[CLS]'] = 0
df_test['[CLS]'] = 0

In [6]:
import random
print("Train:", df_train.shape, df_train['baby_id'].nunique())
print("Validaiton:", df_val.shape, df_val['baby_id'].nunique())

Train: (14093, 25) 9641
Validaiton: (4647, 25) 3213


## Remove baby_id and results

In [7]:
exclude_cols = ['baby_id', 'pcr_result']
cols = [x for x in df_train.columns if x not in exclude_cols]

# move [CLS] at first
cols = ['[CLS]'] + [x for x in cols if x !='[CLS]']

df_train_gt = df_train[['pcr_result']]
df_train_input = df_train[cols]
df_val_gt = df_val[['pcr_result']]
df_val_input = df_val[cols]
df_test_gt = df_test[['pcr_result']]
df_test_input = df_test[cols]


In [8]:
cols

['[CLS]',
 'cough',
 'fever',
 'sore_throat',
 'shortness_of_breath',
 'head_ache',
 'runny_nose',
 'muscle_pain',
 'chills',
 'loss_of_taste',
 'loss_of_smell',
 'sputum',
 'chest_pain',
 'indication_other',
 'indication_abroad',
 'indication_contact',
 'global_confirmed_ratio',
 'confirmed_ratio',
 'sigungu_confirmed_ratio',
 'mask',
 'gender',
 'age_ratio',
 'weekday']

# Make category values

In [9]:
from model.attention_model import CategoricalAttentionModel
from model.utils import get_dict_category_from_dataset
from model.utils import get_category_key, create_cat_and_intensity_from_df

In [10]:
df_trainval = pd.concat([df_train, df_val], axis=0)
print(df_trainval.shape)

dict_category, df_trainval_typed = get_dict_category_from_dataset(df_trainval[cols])
_, df_train_typed = get_dict_category_from_dataset(df_train[cols])
_, df_val_typed = get_dict_category_from_dataset(df_val[cols])
_, df_test_typed = get_dict_category_from_dataset(df_test[cols])
dict_category

(18740, 25)
[CLS] category [0] ...
cough category [1 0] ...
fever category [0 1] ...
sore_throat category [0 1] ...
shortness_of_breath category [0 1] ...
head_ache category [1 0] ...
runny_nose category [0 1] ...
muscle_pain category [0 1] ...
chills category [0 1] ...
loss_of_taste category [0 1] ...
loss_of_smell category [0 1] ...
sputum category [1 0] ...
chest_pain category [0 1] ...
indication_other category [0 1] ...
indication_abroad category [0 1] ...
indication_contact category [1 0] ...
global_confirmed_ratio float [0.1733114  0.17900909 0.13149977 0.14631498 0.15655098 0.17425644
 0.17103502 0.16990724 0.12749546 0.14885249]
confirmed_ratio float [0.00795568 0.00861396 0.00825183 0.00797017 0.01154644 0.01142734
 0.0113018  0.01122937 0.01076423 0.00895517]
sigungu_confirmed_ratio float [0.01298674 0.01308374 0.         0.01324623 0.01342084 0.0135712
 0.01798011 0.01397984 0.01779546 0.0141302 ]
mask category [1 0] ...
gender category [0. 1.] ...
age_ratio float [0.18 0.1

{'[CLS]_0.0': 0,
 'cough_1.0': 1,
 'cough_0.0': 2,
 'fever_0.0': 3,
 'fever_1.0': 4,
 'sore_throat_0.0': 5,
 'sore_throat_1.0': 6,
 'shortness_of_breath_0.0': 7,
 'shortness_of_breath_1.0': 8,
 'head_ache_1.0': 9,
 'head_ache_0.0': 10,
 'runny_nose_0.0': 11,
 'runny_nose_1.0': 12,
 'muscle_pain_0.0': 13,
 'muscle_pain_1.0': 14,
 'chills_0.0': 15,
 'chills_1.0': 16,
 'loss_of_taste_0.0': 17,
 'loss_of_taste_1.0': 18,
 'loss_of_smell_0.0': 19,
 'loss_of_smell_1.0': 20,
 'sputum_1.0': 21,
 'sputum_0.0': 22,
 'chest_pain_0.0': 23,
 'chest_pain_1.0': 24,
 'indication_other_0.0': 25,
 'indication_other_1.0': 26,
 'indication_abroad_0.0': 27,
 'indication_abroad_1.0': 28,
 'indication_contact_1.0': 29,
 'indication_contact_0.0': 30,
 'global_confirmed_ratio': 31,
 'confirmed_ratio': 32,
 'sigungu_confirmed_ratio': 33,
 'mask_1.0': 34,
 'mask_0.0': 35,
 'gender_0.0': 36,
 'gender_1.0': 37,
 'age_ratio': 38,
 'weekday_3.0': 39,
 'weekday_4.0': 40,
 'weekday_5.0': 41,
 'weekday_0.0': 42,
 'weekd

### category 값, intensity 값 생성

### train 데이터 먼저

In [11]:
df_train_category, df_train_intensity = create_cat_and_intensity_from_df(df_train_typed, dict_category)

display(df_train_category.sample(10))
display(df_train_intensity.sample(10))

[CLS]  cough  fever  sore_throat  shortness_of_breath  head_ache  \
581      0.0    1.0    3.0          6.0                  7.0        9.0   
10502    0.0    1.0    3.0          6.0                  7.0        9.0   
13159    0.0    1.0    3.0          5.0                  7.0       10.0   
6647     0.0    1.0    3.0          6.0                  7.0        9.0   
10084    0.0    1.0    4.0          6.0                  8.0        9.0   
1372     0.0    1.0    3.0          6.0                  7.0        9.0   
11362    0.0    2.0    3.0          5.0                  7.0       10.0   
4822     0.0    1.0    4.0          6.0                  7.0        9.0   
4163     0.0    1.0    3.0          6.0                  7.0        9.0   
3332     0.0    1.0    3.0          6.0                  7.0        9.0   

       runny_nose  muscle_pain  chills  loss_of_taste  loss_of_smell  sputum  \
581          12.0         13.0    15.0           17.0           19.0    21.0   
10502        12.0         13.0    15.0           17.0           19.0    22.0   
13159        11.0         13.0    15.0           17.0           19.0    22.0   
6647         11.0         14.0    15.0           17.0           19.0    21.0   
10084        12.0         13.0    15.0           18.0           20.0    21.0   
1372         11.0         13.0    16.0           17.0           19.0    21.0   
11362        11.0         13.0    15.0           17.0           19.0    22.0   
4822         12.0         13.0    15.0           17.0           19.0    21.0   
4163         11.0         13.0    15.0           17.0           19.0    21.0   
3332         12.0         13.0    15.0           17.0           19.0    22.0   

       chest_pain  indication_other  indication_abroad  indication_contact  \
581          24.0              26.0               27.0                30.0   
10502        23.0              25.0               27.0                29.0   
13159        23.0              26.0               27.0                30.0   
6647         23.0              25.0               27.0                29.0   
10084        24.0              26.0               27.0                30.0   
1372         23.0              25.0               27.0                29.0   
11362        23.0              26.0               27.0                30.0   
4822         23.0              26.0               27.0                30.0   
4163         23.0              25.0               27.0                29.0   
3332         23.0              26.0               27.0                30.0   

       global_confirmed_ratio  confirmed_ratio  sigungu_confirmed_ratio  mask  \
581                      31.0             32.0                     33.0  35.0   
10502                    31.0             32.0                     33.0  34.0   
13159                    31.0             32.0                     33.0  34.0   
6647                     31.0             32.0                     33.0  34.0   
10084                    31.0             32.0                     33.0  35.0   
1372                     31.0             32.0                     33.0  34.0   
11362                    31.0             32.0                     33.0  35.0   
4822                     31.0             32.0                     33.0  35.0   
4163                     31.0             32.0                     33.0  34.0   
3332                     31.0             32.0                     33.0  34.0   

       gender  age_ratio  weekday  
581      37.0       38.0     45.0  
10502    37.0       38.0     43.0  
13159    36.0       38.0     42.0  
6647     36.0       38.0     41.0  
10084    37.0       38.0     44.0  
1372     36.0       38.0     41.0  
11362    37.0       38.0     45.0  
4822     36.0       38.0     39.0  
4163     37.0       38.0     43.0  
3332     36.0       38.0     45.0

[CLS]  cough  fever  sore_throat  shortness_of_breath  head_ache  \
10266    1.0    1.0    1.0          1.0                  1.0        1.0   
5162     1.0    1.0    1.0          1.0                  1.0        1.0   
1585     1.0    1.0    1.0          1.0                  1.0        1.0   
9622     1.0    1.0    1.0          1.0                  1.0        1.0   
10618    1.0    1.0    1.0          1.0                  1.0        1.0   
10474    1.0    1.0    1.0          1.0                  1.0        1.0   
4764     1.0    1.0    1.0          1.0                  1.0        1.0   
11988    1.0    1.0    1.0          1.0                  1.0        1.0   
12438    1.0    1.0    1.0          1.0                  1.0        1.0   
5214     1.0    1.0    1.0          1.0                  1.0        1.0   

       runny_nose  muscle_pain  chills  loss_of_taste  loss_of_smell  sputum  \
10266         1.0          1.0     1.0            1.0            1.0     1.0   
5162          1.0          1.0     1.0            1.0            1.0     1.0   
1585          1.0          1.0     1.0            1.0            1.0     1.0   
9622          1.0          1.0     1.0            1.0            1.0     1.0   
10618         1.0          1.0     1.0            1.0            1.0     1.0   
10474         1.0          1.0     1.0            1.0            1.0     1.0   
4764          1.0          1.0     1.0            1.0            1.0     1.0   
11988         1.0          1.0     1.0            1.0            1.0     1.0   
12438         1.0          1.0     1.0            1.0            1.0     1.0   
5214          1.0          1.0     1.0            1.0            1.0     1.0   

       chest_pain  indication_other  indication_abroad  indication_contact  \
10266         1.0               1.0                1.0                 1.0   
5162          1.0               1.0                1.0                 1.0   
1585          1.0               1.0                1.0                 1.0   
9622          1.0               1.0                1.0                 1.0   
10618         1.0               1.0                1.0                 1.0   
10474         1.0               1.0                1.0                 1.0   
4764          1.0               1.0                1.0                 1.0   
11988         1.0               1.0                1.0                 1.0   
12438         1.0               1.0                1.0                 1.0   
5214          1.0               1.0                1.0                 1.0   

       global_confirmed_ratio  confirmed_ratio  sigungu_confirmed_ratio  mask  \
10266                0.170558         0.173634                 0.000000   1.0   
5162                 0.425722         0.538707                 0.232699   1.0   
1585                 0.300265         0.339139                 0.000000   1.0   
9622                 0.232620         0.339080                 0.000000   1.0   
10618                0.197120         0.121378                 0.323654   1.0   
10474                0.117492         0.190635                 0.000000   1.0   
4764                 0.508594         0.655087                 0.200437   1.0   
11988                0.248690         0.066428                 0.413265   1.0   
12438                0.352172         0.181642                 0.429810   1.0   
5214                 0.425722         0.538707                 0.197727   1.0   

       gender  age_ratio  weekday  
10266     1.0       0.46      1.0  
5162      1.0       0.31      1.0  
1585      1.0       0.39      1.0  
9622      1.0       0.47      1.0  
10618     1.0       0.31      1.0  
10474     1.0       0.30      1.0  
4764      1.0       0.29      1.0  
11988     1.0       0.32      1.0  
12438     1.0       0.63      1.0  
5214      1.0       0.35      1.0

예시로 sore_throat id값 확인해봄

In [12]:
size_and_ratio(df_train_category, 'sore_throat')

Sum : 14093 (2,)


size     ratio
sore_throat                
6.0          7723  0.548003
5.0          6370  0.451997

### df_val에서 df_cat값과 df_intensity 값 생성

In [13]:
df_val_category, df_val_intensity = create_cat_and_intensity_from_df(df_val_typed, dict_category)


### df_test에서도 마찬가지로 생성

In [14]:
df_test_category, df_test_intensity = create_cat_and_intensity_from_df(df_test_typed, dict_category)


In [15]:
train_np_cat = df_train_category.values
train_np_ins = df_train_intensity.values
train_np_gt = df_train_gt[['pcr_result']].values

val_np_cat = df_val_category.values
val_np_ins = df_val_intensity.values
val_np_gt = df_val_gt[['pcr_result']].values

test_np_cat = df_test_category.values
test_np_ins = df_test_intensity.values
test_np_gt = df_test_gt[['pcr_result']].values

train_np_gt, val_np_gt, test_np_gt

(array([[0],
        [0],
        [0],
        ...,
        [1],
        [0],
        [0]]),
 array([[0],
        [0],
        [0],
        ...,
        [0],
        [1],
        [0]]),
 array([[0],
        [0],
        [0],
        ...,
        [1],
        [0],
        [1]]))

In [16]:
train_input = [train_np_cat.copy(), train_np_ins.copy()]
train_gt = train_np_gt.copy()

valid_input = [val_np_cat.copy(), val_np_ins.copy()]
valid_gt = val_np_gt.copy()

test_input = [test_np_cat.copy(), test_np_ins.copy()]
test_gt = test_np_gt.copy()


In [17]:
print(train_input[0].shape, valid_input[0].shape, test_input[0].shape)
print(train_gt.shape, valid_gt.shape, test_gt.shape)

(14093, 23) (4647, 23) (4586, 23)
(14093, 1) (4647, 1) (4586, 1)


In [18]:
print("# of train data positive: ", train_gt.sum())
print("# of train data negative: ", train_gt.shape[0] - train_gt.sum())
print("ratio of P/N: ", train_gt.sum()/(train_gt.shape[0] - train_gt.sum()))
print("")

print("# of valid data positive: ", valid_gt.sum())
print("# of valid data negative: ", valid_gt.shape[0] - valid_gt.sum())
print("ratio of P/N: ", valid_gt.sum()/(valid_gt.shape[0] - valid_gt.sum()))
print("")

print("# of test data positive: ", test_gt.sum())
print("# of test data negative: ", test_gt.shape[0] - test_gt.sum())
print("ratio of P/N: ", test_gt.sum()/(test_gt.shape[0] - test_gt.sum()))

# of train data positive:  10063
# of train data negative:  4030
ratio of P/N:  2.4970223325062033

# of valid data positive:  3415
# of valid data negative:  1232
ratio of P/N:  2.7719155844155843

# of test data positive:  3332
# of test data negative:  1254
ratio of P/N:  2.657097288676236


### Check dict_category

In [19]:
dict_category

{'[CLS]_0.0': 0,
 'cough_1.0': 1,
 'cough_0.0': 2,
 'fever_0.0': 3,
 'fever_1.0': 4,
 'sore_throat_0.0': 5,
 'sore_throat_1.0': 6,
 'shortness_of_breath_0.0': 7,
 'shortness_of_breath_1.0': 8,
 'head_ache_1.0': 9,
 'head_ache_0.0': 10,
 'runny_nose_0.0': 11,
 'runny_nose_1.0': 12,
 'muscle_pain_0.0': 13,
 'muscle_pain_1.0': 14,
 'chills_0.0': 15,
 'chills_1.0': 16,
 'loss_of_taste_0.0': 17,
 'loss_of_taste_1.0': 18,
 'loss_of_smell_0.0': 19,
 'loss_of_smell_1.0': 20,
 'sputum_1.0': 21,
 'sputum_0.0': 22,
 'chest_pain_0.0': 23,
 'chest_pain_1.0': 24,
 'indication_other_0.0': 25,
 'indication_other_1.0': 26,
 'indication_abroad_0.0': 27,
 'indication_abroad_1.0': 28,
 'indication_contact_1.0': 29,
 'indication_contact_0.0': 30,
 'global_confirmed_ratio': 31,
 'confirmed_ratio': 32,
 'sigungu_confirmed_ratio': 33,
 'mask_1.0': 34,
 'mask_0.0': 35,
 'gender_0.0': 36,
 'gender_1.0': 37,
 'age_ratio': 38,
 'weekday_3.0': 39,
 'weekday_4.0': 40,
 'weekday_5.0': 41,
 'weekday_0.0': 42,
 'weekd

## Import model

In [46]:
from model.base_dataloader import IsraelDataLoader, IsraelDatasetWithIntensity
from model.utils import run_validation

In [47]:
print("cat value:", train_input[0].shape)
print("intensity value:", train_input[1].shape)
print("Ground truth value:", train_gt.shape)

cat value: (14093, 23)
intensity value: (14093, 23)
Ground truth value: (14093, 1)


# Dataset, data_loader

In [48]:
import logging

logging.basicConfig(level=logging.DEBUG)
logger = logging.getLogger(__name__)

In [49]:
# creat dataset

train_dataset = IsraelDatasetWithIntensity(
    train_np_cat,
    train_np_ins,
    train_np_gt,
    dict_category
)

val_dataset = IsraelDatasetWithIntensity(
    val_np_cat,
    val_np_ins,
    val_np_gt,
    dict_category
)

test_dataset = IsraelDatasetWithIntensity(
    test_np_cat, 
    test_np_ins,
    test_np_gt,
    dict_category
)

In [ ]:
def save_model(config_name, model, epoch):
    save_path = f"./train_data/{model.__class__.__name__}_{config_name}_{epoch:04d}.pth"
    print("save_path", save_path)
    torch.save(model.state_dict(), save_path)
    print("Success to save to : ", save_path)
    return model

### Simple attention

In [263]:
from model import simple_attention

In [277]:
batch_size = 128
epochs = 30000

train_loader = IsraelDataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_loader = IsraelDataLoader(val_dataset, batch_size=batch_size, shuffle=False)

len_seq = train_input[0].shape[1]
print("len_seq:", len_seq)
d_model = 16
n_head = 1
n_layer = 1
lr = 1e-4

model = simple_attention.CategoricalAttentionSimpleModel(
    dict_category=dict_category,
    d_model=d_model,
    n_head=n_head,
    len_seq=len_seq
)

model.eval()

print("d_model:", model.d_model, "n_head:", model.n_head, 'len_seq:', model.len_seq)
loss_func = nn.BCELoss(reduction='mean')
optimizer = optim.RAdam(model.parameters(), lr=lr)
config_name = f"layer{n_layer}_dmodel{d_model}_nhead{n_head}_lr{lr}"

train_log = dict()
val_log = dict()

val_metrics = {
    "loss": loss_func,
    'auc': lambda pred, gt: roc_auc_score(gt.numpy(), pred.numpy())
}


    

len_seq: 23
d_model: 16 n_head: 1 len_seq: 23


In [278]:
model

CategoricalAttentionSimpleModel(
  (cat_embedding): Linear(in_features=46, out_features=16, bias=True)
  (fc_key): Linear(in_features=16, out_features=16, bias=True)
  (fc_query): Linear(in_features=16, out_features=16, bias=True)
  (fc_value): Linear(in_features=16, out_features=16, bias=True)
  (multihead_attn): MultiheadAttention(
    (out_proj): NonDynamicallyQuantizableLinear(in_features=16, out_features=16, bias=True)
  )
  (final_fc): Linear(in_features=16, out_features=1, bias=True)
  (final_sigmoid): Sigmoid()
)

### Test with very small dataset (2 datapoints)

In [279]:
val_np_cat[7:9],    val_np_ins[7:9],    val_np_gt[7:9],

(array([[ 0.,  2.,  3.,  5.,  7., 10., 11., 13., 15., 17., 19., 22., 23.,
         26., 27., 30., 31., 32., 33., 34., 37., 38., 39.],
        [ 0.,  1.,  3.,  5.,  7., 10., 11., 13., 15., 17., 19., 22., 23.,
         26., 27., 30., 31., 32., 33., 34., 37., 38., 40.]]),
 array([[1.        , 1.        , 1.        , 1.        , 1.        ,
         1.        , 1.        , 1.        , 1.        , 1.        ,
         1.        , 1.        , 1.        , 1.        , 1.        ,
         1.        , 0.18225966, 0.01196491, 0.        , 1.        ,
         1.        , 0.41      , 1.        ],
        [1.        , 1.        , 1.        , 1.        , 1.        ,
         1.        , 1.        , 1.        , 1.        , 1.        ,
         1.        , 1.        , 1.        , 1.        , 1.        ,
         1.        , 0.18804529, 0.01177016, 0.02688911, 1.        ,
         1.        , 0.25      , 1.        ]]),
 array([[0],
        [1]]))

In [280]:
small_test_dataset = IsraelDatasetWithIntensity(
    val_np_cat[7:9],
    val_np_ins[7:9],
    val_np_gt[7:9],
    dict_category
)

for i in range(10000):
    small_test_loader = IsraelDataLoader(small_test_dataset, batch_size=batch_size, shuffle=False)
    result_info = model.train_on_epoch(i, small_test_loader, model, loss_func, optimizer)


INFO:model.base_model:Epoch Step: 0 Train Loss: 0.694186270236969 elapsed: 0.0035219192504882812
INFO:model.base_model:Epoch Step: 1 Train Loss: 0.6941860914230347 elapsed: 0.0022530555725097656
INFO:model.base_model:Epoch Step: 2 Train Loss: 0.6941860318183899 elapsed: 0.001995086669921875
INFO:model.base_model:Epoch Step: 3 Train Loss: 0.6941858530044556 elapsed: 0.002009153366088867
INFO:model.base_model:Epoch Step: 4 Train Loss: 0.6941856145858765 elapsed: 0.001561880111694336
INFO:model.base_model:Epoch Step: 5 Train Loss: 0.6941852569580078 elapsed: 0.0020020008087158203
INFO:model.base_model:Epoch Step: 6 Train Loss: 0.694184422492981 elapsed: 0.0018601417541503906
INFO:model.base_model:Epoch Step: 7 Train Loss: 0.694183349609375 elapsed: 0.002974987030029297
INFO:model.base_model:Epoch Step: 8 Train Loss: 0.6941820979118347 elapsed: 0.0023348331451416016
INFO:model.base_model:Epoch Step: 9 Train Loss: 0.6941806077957153 elapsed: 0.002583026885986328
INFO:model.base_model:Epoch 

INFO:model.base_model:Epoch Step: 84 Train Loss: 0.6937612295150757 elapsed: 0.0018947124481201172
INFO:model.base_model:Epoch Step: 85 Train Loss: 0.693753719329834 elapsed: 0.0018811225891113281
INFO:model.base_model:Epoch Step: 86 Train Loss: 0.6937459707260132 elapsed: 0.0017528533935546875
INFO:model.base_model:Epoch Step: 87 Train Loss: 0.6937383413314819 elapsed: 0.0017468929290771484
INFO:model.base_model:Epoch Step: 88 Train Loss: 0.6937307715415955 elapsed: 0.0019431114196777344
INFO:model.base_model:Epoch Step: 89 Train Loss: 0.6937230825424194 elapsed: 0.001967906951904297
INFO:model.base_model:Epoch Step: 90 Train Loss: 0.693715512752533 elapsed: 0.0019218921661376953
INFO:model.base_model:Epoch Step: 91 Train Loss: 0.6937078237533569 elapsed: 0.002259969711303711
INFO:model.base_model:Epoch Step: 92 Train Loss: 0.6937001943588257 elapsed: 0.0020351409912109375
INFO:model.base_model:Epoch Step: 93 Train Loss: 0.6936925649642944 elapsed: 0.0022399425506591797
INFO:model.bas

INFO:model.base_model:Epoch Step: 167 Train Loss: 0.6932262778282166 elapsed: 0.0016279220581054688
INFO:model.base_model:Epoch Step: 168 Train Loss: 0.6932222843170166 elapsed: 0.0015139579772949219
INFO:model.base_model:Epoch Step: 169 Train Loss: 0.6932185888290405 elapsed: 0.0017468929290771484
INFO:model.base_model:Epoch Step: 170 Train Loss: 0.6932147741317749 elapsed: 0.0016438961029052734
INFO:model.base_model:Epoch Step: 171 Train Loss: 0.6932111978530884 elapsed: 0.0015749931335449219
INFO:model.base_model:Epoch Step: 172 Train Loss: 0.6932076215744019 elapsed: 0.0015568733215332031
INFO:model.base_model:Epoch Step: 173 Train Loss: 0.6932041645050049 elapsed: 0.0018038749694824219
INFO:model.base_model:Epoch Step: 174 Train Loss: 0.6932008266448975 elapsed: 0.0016961097717285156
INFO:model.base_model:Epoch Step: 175 Train Loss: 0.6931976079940796 elapsed: 0.001699209213256836
INFO:model.base_model:Epoch Step: 176 Train Loss: 0.6931943893432617 elapsed: 0.0017306804656982422
I

INFO:model.base_model:Epoch Step: 250 Train Loss: 0.6932631731033325 elapsed: 0.0016028881072998047
INFO:model.base_model:Epoch Step: 251 Train Loss: 0.693268358707428 elapsed: 0.0017580986022949219
INFO:model.base_model:Epoch Step: 252 Train Loss: 0.693273663520813 elapsed: 0.0016140937805175781
INFO:model.base_model:Epoch Step: 253 Train Loss: 0.6932790279388428 elapsed: 0.0016880035400390625
INFO:model.base_model:Epoch Step: 254 Train Loss: 0.6932845115661621 elapsed: 0.0016393661499023438
INFO:model.base_model:Epoch Step: 255 Train Loss: 0.6932900547981262 elapsed: 0.0019130706787109375
INFO:model.base_model:Epoch Step: 256 Train Loss: 0.6932957172393799 elapsed: 0.0016300678253173828
INFO:model.base_model:Epoch Step: 257 Train Loss: 0.6933015584945679 elapsed: 0.0018420219421386719
INFO:model.base_model:Epoch Step: 258 Train Loss: 0.6933073997497559 elapsed: 0.0016660690307617188
INFO:model.base_model:Epoch Step: 259 Train Loss: 0.6933133602142334 elapsed: 0.001725912094116211
INF

INFO:model.base_model:Epoch Step: 333 Train Loss: 0.6938447952270508 elapsed: 0.0016040802001953125
INFO:model.base_model:Epoch Step: 334 Train Loss: 0.693850576877594 elapsed: 0.0016748905181884766
INFO:model.base_model:Epoch Step: 335 Train Loss: 0.6938562393188477 elapsed: 0.0033118724822998047
INFO:model.base_model:Epoch Step: 336 Train Loss: 0.6938617825508118 elapsed: 0.0054929256439208984
INFO:model.base_model:Epoch Step: 337 Train Loss: 0.6938672065734863 elapsed: 0.005788087844848633
INFO:model.base_model:Epoch Step: 338 Train Loss: 0.6938725113868713 elapsed: 0.0022361278533935547
INFO:model.base_model:Epoch Step: 339 Train Loss: 0.6938776969909668 elapsed: 0.001993894577026367
INFO:model.base_model:Epoch Step: 340 Train Loss: 0.6938827037811279 elapsed: 0.002004861831665039
INFO:model.base_model:Epoch Step: 341 Train Loss: 0.6938876509666443 elapsed: 0.0020880699157714844
INFO:model.base_model:Epoch Step: 342 Train Loss: 0.6938924789428711 elapsed: 0.0022749900817871094
INFO

...

INFO:model.base_model:Epoch Step: 9607 Train Loss: 0.6956931352615356 elapsed: 0.0017130374908447266
INFO:model.base_model:Epoch Step: 9608 Train Loss: 0.6956621408462524 elapsed: 0.0018198490142822266
INFO:model.base_model:Epoch Step: 9609 Train Loss: 0.6956309080123901 elapsed: 0.0017099380493164062
INFO:model.base_model:Epoch Step: 9610 Train Loss: 0.695599377155304 elapsed: 0.0016109943389892578
INFO:model.base_model:Epoch Step: 9611 Train Loss: 0.6955676674842834 elapsed: 0.0016429424285888672
INFO:model.base_model:Epoch Step: 9612 Train Loss: 0.6955357193946838 elapsed: 0.0016489028930664062
INFO:model.base_model:Epoch Step: 9613 Train Loss: 0.6955035924911499 elapsed: 0.001806020736694336
INFO:model.base_model:Epoch Step: 9614 Train Loss: 0.6954712867736816 elapsed: 0.0016760826110839844
INFO:model.base_model:Epoch Step: 9615 Train Loss: 0.6954387426376343 elapsed: 0.0018818378448486328
INFO:model.base_model:Epoch Step: 9616 Train Loss: 0.6954060792922974 elapsed: 0.001486778259

INFO:model.base_model:Epoch Step: 9689 Train Loss: 0.6933338642120361 elapsed: 0.0018148422241210938
INFO:model.base_model:Epoch Step: 9690 Train Loss: 0.6933192014694214 elapsed: 0.0018799304962158203
INFO:model.base_model:Epoch Step: 9691 Train Loss: 0.6933050155639648 elapsed: 0.0018410682678222656
INFO:model.base_model:Epoch Step: 9692 Train Loss: 0.693291425704956 elapsed: 0.0017957687377929688
INFO:model.base_model:Epoch Step: 9693 Train Loss: 0.6932784914970398 elapsed: 0.0015969276428222656
INFO:model.base_model:Epoch Step: 9694 Train Loss: 0.6932660341262817 elapsed: 0.001703023910522461
INFO:model.base_model:Epoch Step: 9695 Train Loss: 0.6932542324066162 elapsed: 0.001569986343383789
INFO:model.base_model:Epoch Step: 9696 Train Loss: 0.6932430267333984 elapsed: 0.0026102066040039062
INFO:model.base_model:Epoch Step: 9697 Train Loss: 0.6932324171066284 elapsed: 0.0016760826110839844
INFO:model.base_model:Epoch Step: 9698 Train Loss: 0.6932224035263062 elapsed: 0.0015289783477

INFO:model.base_model:Epoch Step: 9771 Train Loss: 0.6942089796066284 elapsed: 0.0017321109771728516
INFO:model.base_model:Epoch Step: 9772 Train Loss: 0.6942442655563354 elapsed: 0.0019309520721435547
INFO:model.base_model:Epoch Step: 9773 Train Loss: 0.6942800283432007 elapsed: 0.0018239021301269531
INFO:model.base_model:Epoch Step: 9774 Train Loss: 0.6943161487579346 elapsed: 0.0017910003662109375
INFO:model.base_model:Epoch Step: 9775 Train Loss: 0.6943528652191162 elapsed: 0.0017042160034179688
INFO:model.base_model:Epoch Step: 9776 Train Loss: 0.6943899393081665 elapsed: 0.0016551017761230469
INFO:model.base_model:Epoch Step: 9777 Train Loss: 0.694427490234375 elapsed: 0.001766204833984375
INFO:model.base_model:Epoch Step: 9778 Train Loss: 0.6944653987884521 elapsed: 0.0017867088317871094
INFO:model.base_model:Epoch Step: 9779 Train Loss: 0.6945037841796875 elapsed: 0.0018038749694824219
INFO:model.base_model:Epoch Step: 9780 Train Loss: 0.6945425271987915 elapsed: 0.001955032348

INFO:model.base_model:Epoch Step: 9853 Train Loss: 0.6976787447929382 elapsed: 0.0017688274383544922
INFO:model.base_model:Epoch Step: 9854 Train Loss: 0.69771409034729 elapsed: 0.0015380382537841797
INFO:model.base_model:Epoch Step: 9855 Train Loss: 0.6977488994598389 elapsed: 0.0014231204986572266
INFO:model.base_model:Epoch Step: 9856 Train Loss: 0.6977831125259399 elapsed: 0.0018908977508544922
INFO:model.base_model:Epoch Step: 9857 Train Loss: 0.697816789150238 elapsed: 0.001847982406616211
INFO:model.base_model:Epoch Step: 9858 Train Loss: 0.6978499293327332 elapsed: 0.0017158985137939453
INFO:model.base_model:Epoch Step: 9859 Train Loss: 0.6978824734687805 elapsed: 0.0018429756164550781
INFO:model.base_model:Epoch Step: 9860 Train Loss: 0.6979143619537354 elapsed: 0.0016551017761230469
INFO:model.base_model:Epoch Step: 9861 Train Loss: 0.6979458332061768 elapsed: 0.0015707015991210938
INFO:model.base_model:Epoch Step: 9862 Train Loss: 0.6979765892028809 elapsed: 0.00155282020568

INFO:model.base_model:Epoch Step: 9935 Train Loss: 0.6982314586639404 elapsed: 0.0017781257629394531
INFO:model.base_model:Epoch Step: 9936 Train Loss: 0.6982080936431885 elapsed: 0.001682281494140625
INFO:model.base_model:Epoch Step: 9937 Train Loss: 0.6981841325759888 elapsed: 0.0016388893127441406
INFO:model.base_model:Epoch Step: 9938 Train Loss: 0.6981595754623413 elapsed: 0.0017178058624267578
INFO:model.base_model:Epoch Step: 9939 Train Loss: 0.6981345415115356 elapsed: 0.001628875732421875
INFO:model.base_model:Epoch Step: 9940 Train Loss: 0.6981088519096375 elapsed: 0.0016109943389892578
INFO:model.base_model:Epoch Step: 9941 Train Loss: 0.6980826258659363 elapsed: 0.0016629695892333984
INFO:model.base_model:Epoch Step: 9942 Train Loss: 0.6980559229850769 elapsed: 0.0017118453979492188
INFO:model.base_model:Epoch Step: 9943 Train Loss: 0.6980286836624146 elapsed: 0.0016193389892578125
INFO:model.base_model:Epoch Step: 9944 Train Loss: 0.6980009078979492 elapsed: 0.001734018325

In [ ]:

for epoch in range(epochs):
    # **************** Train ****************
    train_result_info = model.train_on_epoch(epoch, train_loader, model, loss_func, optimizer)
    train_log[f'epoch_train_{epoch}'] = train_result_info
    logger.debug(f"epoch {epoch} train finished. train_result_info:{train_result_info}")
    
    # ************** validation *********************
    val_result = model.validation_on_epoch(epoch, model, val_loader, val_metrics)
    val_log[f'epoch_val_{epoch}'] = val_result
    logger.info(f"epoch {epoch} val result: {val_result}")

    if not val_log:
        best_model = save_model(config_name, model.copy(), epoch)
    elif val_result['auc'] >= max(val_log.values(), key=lambda x : x['auc'])['auc']:
        best_model = save_model(config_name, model.copy(), epoch)


INFO:model.base_model:Epoch Step: 0 Train Loss: 78.20327758789062 elapsed: 0.8567650318145752
DEBUG:base_model:epoch 0 train finished. train_result_info:{'total_n_batch': 110, 'total_train_loss_by_token': tensor(78.2033, grad_fn=<AddBackward0>), 'total_tokens': 2553}
INFO:model.base_model:cur_epoch:0, validation elapsed_time:0.08505606651306152
INFO:base_model:epoch 0 val result: {'loss': tensor(0.6742), 'auc': 0.4935604476051035}


save_path ./train_data/CategoricalAttentionSimpleModel_layer1_dmodel16_nhead1_lr0.0001_0000.pth
Success to save to :  ./train_data/CategoricalAttentionSimpleModel_layer1_dmodel16_nhead1_lr0.0001_0000.pth


INFO:model.base_model:Epoch Step: 1 Train Loss: 71.86639404296875 elapsed: 0.6606976985931396
DEBUG:base_model:epoch 1 train finished. train_result_info:{'total_n_batch': 110, 'total_train_loss_by_token': tensor(71.8664, grad_fn=<AddBackward0>), 'total_tokens': 2553}
INFO:model.base_model:cur_epoch:1, validation elapsed_time:0.08582878112792969
INFO:base_model:epoch 1 val result: {'loss': tensor(0.6067), 'auc': 0.5}


save_path ./train_data/CategoricalAttentionSimpleModel_layer1_dmodel16_nhead1_lr0.0001_0001.pth
Success to save to :  ./train_data/CategoricalAttentionSimpleModel_layer1_dmodel16_nhead1_lr0.0001_0001.pth


INFO:model.base_model:Epoch Step: 2 Train Loss: 67.47532653808594 elapsed: 0.7791690826416016
DEBUG:base_model:epoch 2 train finished. train_result_info:{'total_n_batch': 110, 'total_train_loss_by_token': tensor(67.4753, grad_fn=<AddBackward0>), 'total_tokens': 2553}
INFO:model.base_model:cur_epoch:2, validation elapsed_time:0.2296457290649414
INFO:base_model:epoch 2 val result: {'loss': tensor(0.5874), 'auc': 0.5}


...

INFO:model.base_model:cur_epoch:10356, validation elapsed_time:0.0829308032989502
INFO:base_model:epoch 10356 val result: {'loss': tensor(73.4883), 'auc': 0.5}
INFO:model.base_model:Epoch Step: 10357 Train Loss: 7923.91845703125 elapsed: 0.8498270511627197
DEBUG:base_model:epoch 10357 train finished. train_result_info:{'total_n_batch': 110, 'total_train_loss_by_token': tensor(7923.9185, grad_fn=<AddBackward0>), 'total_tokens': 2553}
INFO:model.base_model:cur_epoch:10357, validation elapsed_time:0.10839700698852539
INFO:base_model:epoch 10357 val result: {'loss': tensor(73.4883), 'auc': 0.5}
INFO:model.base_model:Epoch Step: 10358 Train Loss: 7917.00732421875 elapsed: 0.7561101913452148
DEBUG:base_model:epoch 10358 train finished. train_result_info:{'total_n_batch': 110, 'total_train_loss_by_token': tensor(7917.0073, grad_fn=<AddBackward0>), 'total_tokens': 2553}
INFO:model.base_model:cur_epoch:10358, validation elapsed_time:0.08163189888000488
INFO:base_model:epoch 10358 val result: {'

INFO:model.base_model:cur_epoch:10375, validation elapsed_time:0.08276629447937012
INFO:base_model:epoch 10375 val result: {'loss': tensor(73.4883), 'auc': 0.5}
INFO:model.base_model:Epoch Step: 10376 Train Loss: 7896.27392578125 elapsed: 0.7929761409759521
DEBUG:base_model:epoch 10376 train finished. train_result_info:{'total_n_batch': 110, 'total_train_loss_by_token': tensor(7896.2739, grad_fn=<AddBackward0>), 'total_tokens': 2553}
INFO:model.base_model:cur_epoch:10376, validation elapsed_time:0.10935235023498535
INFO:base_model:epoch 10376 val result: {'loss': tensor(73.4883), 'auc': 0.5}
INFO:model.base_model:Epoch Step: 10377 Train Loss: 7923.91845703125 elapsed: 0.9111018180847168
DEBUG:base_model:epoch 10377 train finished. train_result_info:{'total_n_batch': 110, 'total_train_loss_by_token': tensor(7923.9185, grad_fn=<AddBackward0>), 'total_tokens': 2553}
INFO:model.base_model:cur_epoch:10377, validation elapsed_time:0.11764788627624512
INFO:base_model:epoch 10377 val result: {

INFO:model.base_model:cur_epoch:10394, validation elapsed_time:0.13025712966918945
INFO:base_model:epoch 10394 val result: {'loss': tensor(73.4883), 'auc': 0.5}
INFO:model.base_model:Epoch Step: 10395 Train Loss: 7930.8291015625 elapsed: 0.760991096496582
DEBUG:base_model:epoch 10395 train finished. train_result_info:{'total_n_batch': 110, 'total_train_loss_by_token': tensor(7930.8291, grad_fn=<AddBackward0>), 'total_tokens': 2553}
INFO:model.base_model:cur_epoch:10395, validation elapsed_time:0.08033585548400879
INFO:base_model:epoch 10395 val result: {'loss': tensor(73.4883), 'auc': 0.5}
INFO:model.base_model:Epoch Step: 10396 Train Loss: 7944.6513671875 elapsed: 0.6888470649719238
DEBUG:base_model:epoch 10396 train finished. train_result_info:{'total_n_batch': 110, 'total_train_loss_by_token': tensor(7944.6514, grad_fn=<AddBackward0>), 'total_tokens': 2553}
INFO:model.base_model:cur_epoch:10396, validation elapsed_time:0.08901691436767578
INFO:base_model:epoch 10396 val result: {'lo

INFO:model.base_model:cur_epoch:10413, validation elapsed_time:0.1301712989807129
INFO:base_model:epoch 10413 val result: {'loss': tensor(73.4883), 'auc': 0.5}
INFO:model.base_model:Epoch Step: 10414 Train Loss: 7917.00732421875 elapsed: 0.7522292137145996
DEBUG:base_model:epoch 10414 train finished. train_result_info:{'total_n_batch': 110, 'total_train_loss_by_token': tensor(7917.0073, grad_fn=<AddBackward0>), 'total_tokens': 2553}
INFO:model.base_model:cur_epoch:10414, validation elapsed_time:0.0785210132598877
INFO:base_model:epoch 10414 val result: {'loss': tensor(73.4883), 'auc': 0.5}
INFO:model.base_model:Epoch Step: 10415 Train Loss: 7917.00732421875 elapsed: 0.6406867504119873
DEBUG:base_model:epoch 10415 train finished. train_result_info:{'total_n_batch': 110, 'total_train_loss_by_token': tensor(7917.0073, grad_fn=<AddBackward0>), 'total_tokens': 2553}
INFO:model.base_model:cur_epoch:10415, validation elapsed_time:0.1834549903869629
INFO:base_model:epoch 10415 val result: {'lo

INFO:model.base_model:cur_epoch:10432, validation elapsed_time:0.08118033409118652
INFO:base_model:epoch 10432 val result: {'loss': tensor(73.4883), 'auc': 0.5}
INFO:model.base_model:Epoch Step: 10433 Train Loss: 7930.8291015625 elapsed: 0.7019479274749756
DEBUG:base_model:epoch 10433 train finished. train_result_info:{'total_n_batch': 110, 'total_train_loss_by_token': tensor(7930.8291, grad_fn=<AddBackward0>), 'total_tokens': 2553}
INFO:model.base_model:cur_epoch:10433, validation elapsed_time:0.12673306465148926
INFO:base_model:epoch 10433 val result: {'loss': tensor(73.4883), 'auc': 0.5}
INFO:model.base_model:Epoch Step: 10434 Train Loss: 7917.00732421875 elapsed: 0.8388841152191162
DEBUG:base_model:epoch 10434 train finished. train_result_info:{'total_n_batch': 110, 'total_train_loss_by_token': tensor(7917.0073, grad_fn=<AddBackward0>), 'total_tokens': 2553}
INFO:model.base_model:cur_epoch:10434, validation elapsed_time:0.15594005584716797
INFO:base_model:epoch 10434 val result: {'

## Transformer encoder
3층

In [122]:
from model import transformer_encoder_model


In [117]:


batch_size = 128
epochs = 30000

train_loader = IsraelDataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_loader = IsraelDataLoader(val_dataset, batch_size=batch_size, shuffle=False)

len_seq = train_input[0].shape[1]
print("len_seq:", len_seq)
d_model = 8
n_head = 1
n_layer = 1
lr = 1e-4

encoder_layer = nn.TransformerEncoderLayer(d_model=d_model, nhead=n_head, dropout=0.1)
transformer_encoder = nn.TransformerEncoder(encoder_layer, num_layers=n_layer)
model = transformer_encoder_model.MuliplyIntensityUsingCls(
    transformer_encoder=transformer_encoder,
    dict_category=dict_category,
    len_seq=len_seq,
)

model.eval()

print("d_model:", model.d_model, "n_head:", model.n_head, 'len_seq:', model.len_seq)
loss_func = nn.BCELoss(reduction='mean')
optimizer = optim.RAdam(model.parameters(), lr=lr)
config_name = f"big_layer{n_layer}_dmodel{d_model}_nhead{n_head}_lr{lr}"

train_log = dict()
val_log = dict()

val_metrics = {
    "loss": loss_func,
    'auc': lambda pred, gt: roc_auc_score(gt.numpy(), pred.numpy())
}


    

len_seq: 23
d_model: 8 n_head: 1 len_seq: 23


In [118]:
model

MuliplyIntensityUsingCls(
  (cat_embeding): Embedding(46, 8)
  (transformer_encoder): TransformerEncoder(
    (layers): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiheadAttention(
          (out_proj): NonDynamicallyQuantizableLinear(in_features=8, out_features=8, bias=True)
        )
        (linear1): Linear(in_features=8, out_features=2048, bias=True)
        (dropout): Dropout(p=0.1, inplace=False)
        (linear2): Linear(in_features=2048, out_features=8, bias=True)
        (norm1): LayerNorm((8,), eps=1e-05, elementwise_affine=True)
        (norm2): LayerNorm((8,), eps=1e-05, elementwise_affine=True)
        (dropout1): Dropout(p=0.1, inplace=False)
        (dropout2): Dropout(p=0.1, inplace=False)
      )
    )
  )
  (global_pooling): AvgPool1d(kernel_size=(23,), stride=(23,), padding=(0,))
  (final_fc): Linear(in_features=8, out_features=1, bias=True)
  (final_activation): Sigmoid()
)

In [70]:

for epoch in range(epochs):
    # **************** Train ****************
    train_result_info = transformer_encoder_model.MuliplyIntensityUsingCls.train_on_epoch(epoch, train_loader, model, loss_func, optimizer, verbose=True)
    train_log[f'epoch_train_{epoch}'] = train_result_info
    logger.debug(f"epoch {epoch} train finished. train_result_info:{train_result_info}")
    
    # ************** validation *********************
    val_result = transformer_encoder_model.MuliplyIntensityUsingCls.validation_on_epoch(epoch, model, val_loader, val_metrics)
    val_log[f'epoch_val_{epoch}'] = val_result
    logger.info(f"epoch {epoch} val result: {val_result}")

    if not val_log:
        best_model = save_model(config_name, model.copy(), epoch)
    elif val_result['auc'] >= max(val_log.values(), key=lambda x : x['auc'])['auc']:
        best_model = save_model(config_name, model.copy(), epoch)


Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128, 1])
after activation out:  torch.Size([128, 1])
Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128, 1])
after activation out:  torch.Size([128, 1])
Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128, 1])
after activation out:  torch.Size([128, 1])
Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128, 1])
after activation out:  torch.Size([128, 1])
Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128, 1])
after activation out:  torch.Size([128, 1])
Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128

Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128, 1])
after activation out:  torch.Size([128, 1])
Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128, 1])
after activation out:  torch.Size([128, 1])
Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128, 1])
after activation out:  torch.Size([128, 1])
Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128, 1])
after activation out:  torch.Size([128, 1])
Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128, 1])
after activation out:  torch.Size([128, 1])
Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128

Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128, 1])
after activation out:  torch.Size([128, 1])
Before final top:  torch.Size([128, 23, 16])
first token vector:  torch.Size([128, 16])
after final top out:  torch.Size([128, 1])
after activation out:  torch.Size([128, 1])


KeyboardInterrupt: 

In [71]:
val_result

{'loss': tensor(0.5794), 'auc': 0.5}

In [27]:
## Check the best model's validation performance
display(val_log)
print("Best validation performance:", max(val_log.values(), key=lambda x : x['auc']))

## Check the best model's test performance
test_loader = IsraelDataLoader(test_dataset, batch_size=64, shuffle=False)

best_model.eval()
test_result = best_model.validation_on_epoch(epoch, best_model, test_loader, val_metrics)
test_result

{'epoch_val_0': {'loss': tensor(0.6084), 'auc': 0.5},
 'epoch_val_1': {'loss': tensor(0.6134), 'auc': 0.5},
 'epoch_val_2': {'loss': tensor(0.5807), 'auc': 0.5},
 'epoch_val_3': {'loss': tensor(0.5815), 'auc': 0.5},
 'epoch_val_4': {'loss': tensor(0.5784), 'auc': 0.5},
 'epoch_val_5': {'loss': tensor(0.5784), 'auc': 0.5},
 'epoch_val_6': {'loss': tensor(0.5786), 'auc': 0.5},
 'epoch_val_7': {'loss': tensor(0.5957), 'auc': 0.5},
 'epoch_val_8': {'loss': tensor(0.6658), 'auc': 0.5},
 'epoch_val_9': {'loss': tensor(0.7118), 'auc': 0.5},
 'epoch_val_10': {'loss': tensor(0.5811), 'auc': 0.5},
 'epoch_val_11': {'loss': tensor(0.6707), 'auc': 0.5},
 'epoch_val_12': {'loss': tensor(0.6391), 'auc': 0.5},
 'epoch_val_13': {'loss': tensor(0.6086), 'auc': 0.5},
 'epoch_val_14': {'loss': tensor(0.8430), 'auc': 0.5},
 'epoch_val_15': {'loss': tensor(0.6344), 'auc': 0.5},
 'epoch_val_16': {'loss': tensor(0.7059), 'auc': 0.5},
 'epoch_val_17': {'loss': tensor(0.6741), 'auc': 0.5},
 'epoch_val_18': {'l

Best validation performance: {'loss': tensor(0.6546), 'auc': 0.5064395523948965}


INFO:model.base_model:cur_epoch:299, validation elapsed_time:0.8442840576171875


{'loss': tensor(2.1221), 'auc': 0.5074170816652019}

### 6층 짜리로 한번 가보자